In [1]:
import datetime
import math
import nltk
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.porter import *
import numpy as np
import pandas as pd
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import string

In [2]:
borough_to_cluster = pd.read_csv("./data/borough_to_cluster.csv")

In [4]:
borough_to_cluster.head()

LOCATION  Cluster
0  Barking and Dagenham        1
1                Barnet        1
2                Bexley        1
3                 Brent        2
4               Bromley        1

In [3]:
tweets = pd.read_csv("./data/london_tweets.csv", encoding="latin1")

In [5]:
tweets.head()

id  Name         X          Y  LONGITUDE   LATITUDE  \
0  550226818624942080   NaN -0.262150  51.391407  -0.262150  51.391407   
1  550226827944660992   NaN -0.014891  51.354042  -0.014891  51.354042   
2  550226837537058816   NaN  0.006698  51.532020   0.006698  51.532021   
3  550227214227505152   NaN  0.214417  51.582535   0.214417  51.582535   
4  550227602011856896   NaN -0.104869  51.509530  -0.104869  51.509529   

           MESSAGEDATE     USERID USERSCREENNAME  \
0  31/12/2014 09:47:50  113918054   12Elbestreet   
1  31/12/2014 09:47:53   55872342    MissGee_Pee   
2  31/12/2014 09:47:55  147266450  vinita_ramtri   
3  31/12/2014 09:49:25  518928608  CallumGordon7   
4  31/12/2014 09:50:57  151094999       HevnKISZ   

                                         MESSAGETEXT              LOCATION  \
0  @julieo25 Not yet got tics for Liverpool waiti...  Kingston upon Thames   
1  If it doesn't make you happy by December 31st....               Croydon   
2  @westfieldstrat thanks; and are you open tomor...                Newham   
3                       @WestHam_Central but he is                Havering   
4                    @JJJ_Jeeppy >> #             XD             Southwark   

       HASHTAGS  ISRETWEET             datetime  
0           NaN          0  2014-12-31 09:47:50  
1           NaN          0  2014-12-31 09:47:53  
2           NaN          0  2014-12-31 09:47:55  
3           NaN          0  2014-12-31 09:49:25  
4                        0  2014-12-31 09:50:57

In [6]:
data = tweets.merge(borough_to_cluster, left_on='LOCATION', right_on='LOCATION', how='outer')

In [7]:
data.head()

id  Name         X          Y  LONGITUDE   LATITUDE  \
0  550226818624942080   NaN -0.262150  51.391407  -0.262150  51.391407   
1  550228733014331392   NaN -0.305024  51.427956  -0.305024  51.427956   
2  550212608746606594   NaN -0.261681  51.391760  -0.261681  51.391762   
3  550218811904114688   NaN -0.298933  51.420210  -0.298933  51.420212   
4  550225718060519424   NaN -0.293391  51.416702  -0.293391  51.416702   

           MESSAGEDATE      USERID   USERSCREENNAME  \
0  31/12/2014 09:47:50   113918054     12Elbestreet   
1  31/12/2014 09:55:27   275233035           2bcmel   
2  31/12/2014 08:51:23   113918054     12Elbestreet   
3  31/12/2014 09:16:01  2463405963  mrsclaireismail   
4  31/12/2014 09:43:28   450719269       manda10110   

                                         MESSAGETEXT              LOCATION  \
0  @julieo25 Not yet got tics for Liverpool waiti...  Kingston upon Thames   
1  @pjbish hey dude from bude; U 2! Big hugs to t...  Kingston upon Thames   
2  One of the greatest singers of all time good m...  Kingston upon Thames   
3  @theshores124 We were planning to go down to B...  Kingston upon Thames   
4  @joemcelderry91  Wishing you Health; Love and ...  Kingston upon Thames   

  HASHTAGS  ISRETWEET             datetime  Cluster  
0      NaN          0  2014-12-31 09:47:50        1  
1      NaN          0  2014-12-31 09:55:27        1  
2      NaN          0  2014-12-31 08:51:23        1  
3      NaN          0  2014-12-31 09:16:01        1  
4      NaN          0  2014-12-31 09:43:28        1

In [8]:
def parse_tweets(tweet):

    tweet = re.sub('@[^\s]+','',tweet).strip()
    tweet = re.sub('#[^\s]+','',tweet).strip()
    tweet = re.sub(r'https?:\/\/.*[\r\n]*','',tweet).strip()
    tweet = " ".join(re.findall("[a-zA-Z]+", tweet))
    
    return tweet

In [9]:
data["parsed_tweets"] = data.MESSAGETEXT.apply(lambda tweet: parse_tweets(tweet))

In [18]:
# need to get pos tag
class StemmerTokenizer(object):

    def __init__(self):
        self.stemmer = PorterStemmer()
        
    def __call__(self, doc):
        doc = doc.lower()
        doc = " ".join(re.findall("[a-zA-Z]+", doc))
        tokenized = nltk.word_tokenize(doc)
        nouns = [word for (word, pos) in nltk.pos_tag(tokenized)] 
        return [self.stemmer.stem(t) for t in word_tokenize(doc)]

In [19]:
stemmer = PorterStemmer()

def get_stemmed_tokens(doc):
    is_noun = lambda pos: pos[:2] == 'NN'
    doc = " ".join(re.findall("[a-zA-Z]+", doc))
    tokenized = nltk.word_tokenize(doc)
    nouns = [word for (word, pos) in nltk.pos_tag(tokenized) if is_noun(pos)] 
    return [stemmer.stem(t) for t in word_tokenize(doc)]

In [20]:
data["stemmed_tokens"] = data.parsed_tweets.apply(lambda tweet: get_stemmed_tokens(tweet))

In [30]:
data.head(15)

id  Name         X          Y  LONGITUDE   LATITUDE  \
0   550226818624942080   NaN -0.262150  51.391407  -0.262150  51.391407   
1   550228733014331392   NaN -0.305024  51.427956  -0.305024  51.427956   
2   550212608746606594   NaN -0.261681  51.391760  -0.261681  51.391762   
3   550218811904114688   NaN -0.298933  51.420210  -0.298933  51.420212   
4   550225718060519424   NaN -0.293391  51.416702  -0.293391  51.416702   
5   550226427069865984   NaN -0.261647  51.391495  -0.261647  51.391495   
6   550232427348897792   NaN -0.293364  51.416690  -0.293364  51.416691   
7   550232636313325568   NaN -0.272390  51.365818  -0.272390  51.365818   
8   550219313672900608   NaN -0.295426  51.377610  -0.295426  51.377609   
9   550220685797515265   NaN -0.297143  51.416954  -0.297143  51.416954   
10  550229505303117824   NaN -0.278894  51.406685  -0.278894  51.406685   
11  550230156351397888   NaN -0.272448  51.365818  -0.272448  51.365818   
12  550230922529087492   NaN -0.258486  51.402924  -0.258486  51.402924   
13  550210874645159936   NaN -0.305390  51.392647  -0.305390  51.392647   
14  550214484628082688   NaN -0.295413  51.377613  -0.295413  51.377613   

            MESSAGEDATE      USERID   USERSCREENNAME  \
0   31/12/2014 09:47:50   113918054     12Elbestreet   
1   31/12/2014 09:55:27   275233035           2bcmel   
2   31/12/2014 08:51:23   113918054     12Elbestreet   
3   31/12/2014 09:16:01  2463405963  mrsclaireismail   
4   31/12/2014 09:43:28   450719269       manda10110   
5   31/12/2014 09:46:17   113918054     12Elbestreet   
6   31/12/2014 10:10:08   450719269       manda10110   
7   31/12/2014 10:10:57    37974717        MaybeBeth   
8   31/12/2014 09:18:01   483244499    martinpowell4   
9   31/12/2014 09:23:28   391440046      jessssicatz   
10  31/12/2014 09:58:31   186869847     RosieCahalin   
11  31/12/2014 10:01:06    37974717        MaybeBeth   
12  31/12/2014 10:04:09  1260430994  Fotografia_slub   
13  31/12/2014 08:44:29   802246206       Lau_Gentle   
14  31/12/2014 08:58:50   483244499    martinpowell4   

                                          MESSAGETEXT              LOCATION  \
0   @julieo25 Not yet got tics for Liverpool waiti...  Kingston upon Thames   
1   @pjbish hey dude from bude; U 2! Big hugs to t...  Kingston upon Thames   
2   One of the greatest singers of all time good m...  Kingston upon Thames   
3   @theshores124 We were planning to go down to B...  Kingston upon Thames   
4   @joemcelderry91  Wishing you Health; Love and ...  Kingston upon Thames   
5   @julieo25 the secret is safe with me good job ...  Kingston upon Thames   
6   @joemcelderry91 We'll have to do it again then...  Kingston upon Thames   
7   @alex26stallard You want the puppy; you deal w...  Kingston upon Thames   
8                 @sammyp333 Will be fine thanks       Kingston upon Thames   
9                   mama knows http://t.co/dXXQ2NRrpd  Kingston upon Thames   
10                             http://t.co/UQuNGKPix8  Kingston upon Thames   
11  @alex26stallard learn to pick up poop and then...  Kingston upon Thames   
12  R&A wedding #vsco #vscofilm #vscogood #wroclaw...  Kingston upon Thames   
13    Wore my pyjamas to work this morning      #yolo  Kingston upon Thames   
14  @digdeepdolly @JulieBond1 @BrightonMarathn @Ru...  Kingston upon Thames   

                                             HASHTAGS  ISRETWEET  \
0                                                 NaN          0   
1                                                 NaN          0   
2                                                 NaN          0   
3                                                 NaN          0   
4                                                 NaN          0   
5                                                 NaN          0   
6                                       EvolutionTour          0   
7                                                 NaN          0   
8                                            

In [21]:
target_tokens = ["happi", "new", "year"]

In [31]:
data["is_new_years_tweet"] = data.stemmed_tokens.apply(lambda tokens: any(x in tokens for x in target_tokens))

In [32]:
data.head()

id  Name         X          Y  LONGITUDE   LATITUDE  \
0  550226818624942080   NaN -0.262150  51.391407  -0.262150  51.391407   
1  550228733014331392   NaN -0.305024  51.427956  -0.305024  51.427956   
2  550212608746606594   NaN -0.261681  51.391760  -0.261681  51.391762   
3  550218811904114688   NaN -0.298933  51.420210  -0.298933  51.420212   
4  550225718060519424   NaN -0.293391  51.416702  -0.293391  51.416702   

           MESSAGEDATE      USERID   USERSCREENNAME  \
0  31/12/2014 09:47:50   113918054     12Elbestreet   
1  31/12/2014 09:55:27   275233035           2bcmel   
2  31/12/2014 08:51:23   113918054     12Elbestreet   
3  31/12/2014 09:16:01  2463405963  mrsclaireismail   
4  31/12/2014 09:43:28   450719269       manda10110   

                                         MESSAGETEXT              LOCATION  \
0  @julieo25 Not yet got tics for Liverpool waiti...  Kingston upon Thames   
1  @pjbish hey dude from bude; U 2! Big hugs to t...  Kingston upon Thames   
2  One of the greatest singers of all time good m...  Kingston upon Thames   
3  @theshores124 We were planning to go down to B...  Kingston upon Thames   
4  @joemcelderry91  Wishing you Health; Love and ...  Kingston upon Thames   

  HASHTAGS  ISRETWEET             datetime  Cluster  \
0      NaN          0  2014-12-31 09:47:50        1   
1      NaN          0  2014-12-31 09:55:27        1   
2      NaN          0  2014-12-31 08:51:23        1   
3      NaN          0  2014-12-31 09:16:01        1   
4      NaN          0  2014-12-31 09:43:28        1   

                                       parsed_tweets  \
0  Not yet got tics for Liverpool waiting till Fr...   
1  hey dude from bude U Big hugs to the family an...   
2  One of the greatest singers of all time good m...   
3  We were planning to go down to Bournemouth Fri...   
4  Wishing you Health Love and Laughter for and s...   

                                      stemmed_tokens  is_new_years_tweet  
0  [not, yet, got, tic, for, liverpool, wait, til...               False  
1  [hey, dude, from, bude, U, big, hug, to, the, ...               False  
2  [one, of, the, greatest, singer, of, all, time...               False  
3  [We, were, plan, to, go, down, to, bournemouth...               False  
4  [wish, you, health, love, and, laughter, for, ...               False

In [33]:
new_years_tweets = data[data.is_new_years_tweet == True]

In [34]:
new_years_tweets.head()

id  Name         X          Y  LONGITUDE   LATITUDE  \
14  550214484628082688   NaN -0.295413  51.377613  -0.295413  51.377613   
25  550218423515762688   NaN -0.273753  51.399380  -0.273753  51.399380   
29  550232802722336768   NaN -0.293350  51.416683  -0.293350  51.416683   
31  550216489132101632   NaN -0.273675  51.399395  -0.273675  51.399395   
37  550230273670262785   NaN -0.295399  51.377570  -0.295399  51.377571   

            MESSAGEDATE     USERID USERSCREENNAME  \
14  31/12/2014 08:58:50  483244499  martinpowell4   
25  31/12/2014 09:14:29  365780632    gazzadexy40   
29  31/12/2014 10:11:37  450719269     manda10110   
31  31/12/2014 09:06:48  365780632    gazzadexy40   
37  31/12/2014 10:01:34  483244499  martinpowell4   

                                          MESSAGETEXT              LOCATION  \
14  @digdeepdolly @JulieBond1 @BrightonMarathn @Ru...  Kingston upon Thames   
25  @iamjujun my christmas card from the mighty ye...  Kingston upon Thames   
29  @greesyduck Health and Happiness to you in 201...  Kingston upon Thames   
31  @iamjujun mine has been doing voluntary work f...  Kingston upon Thames   
37  @AdamPrav @AndreTrill @UKRunChat @parkrunUK @O...  Kingston upon Thames   

   HASHTAGS  ISRETWEET             datetime  Cluster  \
14      NaN          0  2014-12-31 08:58:50        1   
25      NaN          0  2014-12-31 09:14:29        1   
29      NaN          0  2014-12-31 10:11:37        1   
31      NaN          0  2014-12-31 09:06:48        1   
37      NaN          0  2014-12-31 10:01:34        1   

                                        parsed_tweets  \
14  Friend at work did Brighton last year it was a...   
25  my christmas card from the mighty year ones Ha...   
29        Health and Happiness to you in too Pete xxx   
31  mine has been doing voluntary work for a chari...   
37  That s something I would like to do next year ...   

                                       stemmed_tokens  is_new_years_tweet  
14  [friend, at, work, did, brighton, last, year, ...                True  
25  [my, christma, card, from, the, mighti, year, ...                True  
29  [health, and, happi, to, you, in, too, pete, xxx]                True  
31  [mine, ha, been, do, voluntari, work, for, a, ...                True  
37  [that, s, someth, I, would, like, to, do, next...                True

In [35]:
cluster_0 = new_years_tweets[new_years_tweets.Cluster == 0]
cluster_1 = new_years_tweets[new_years_tweets.Cluster == 1]
cluster_2 = new_years_tweets[new_years_tweets.Cluster == 2]
cluster_3 = new_years_tweets[new_years_tweets.Cluster == 3]
cluster_4 = new_years_tweets[new_years_tweets.Cluster == 4]

In [36]:
new_years_tweets.to_csv("./data/new_years_tweets_by_cluster.csv")

In [40]:
for idx, row in cluster_2.iterrows():
    print(row)

id                                                   550226469356855296
Name                                                                NaN
X                                                             -0.082229
Y                                                               51.4904
LONGITUDE                                                     -0.082229
LATITUDE                                                        51.4904
MESSAGEDATE                                         31/12/2014 09:46:27
USERID                                                         19785093
USERSCREENNAME                                            Sonic_Screwup
MESSAGETEXT           Sorry just thought I'd offer a balanced view o...
LOCATION                                                      Southwark
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                                            2014-12-31 0

Name: 13188, dtype: object
id                                                   550421017731272704
Name                                                                NaN
X                                                             -0.033828
Y                                                               51.5002
LONGITUDE                                                     -0.033828
LATITUDE                                                        51.5002
MESSAGEDATE                                         31/12/2014 22:39:31
USERID                                                        290345467
USERSCREENNAME                                                 REISSMFC
MESSAGETEXT           New Year's Eve in my room watching Tears of th...
LOCATION                                                      Southwark
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

Name: 14065, dtype: object
id                                                   550373058452942849
Name                                                                NaN
X                                                             -0.076372
Y                                                               51.5036
LONGITUDE                                                     -0.076372
LATITUDE                                                        51.5036
MESSAGEDATE                                         31/12/2014 19:28:57
USERID                                                        546823454
USERSCREENNAME                                                JTAH_1990
MESSAGETEXT           This time last year I had so many hopes and dr...
LOCATION                                                      Southwark
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

id                                          550741844347613184
Name                                                       NaN
X                                                    -0.060027
Y                                                      51.4959
LONGITUDE                                            -0.060027
LATITUDE                                               51.4959
MESSAGEDATE                                01/01/2015 19:54:22
USERID                                               125108379
USERSCREENNAME                                  molliewiddows_
MESSAGETEXT           New year selfie   http://t.co/JA1LRjHpFp
LOCATION                                             Southwark
HASHTAGS                                                   NaN
ISRETWEET                                                    0
datetime                                   2015-01-01 19:54:22
Cluster                                                      2
parsed_tweets                                  New year

Name: 20268, dtype: object
id                                      550242313973559296
Name                                                   NaN
X                                                -0.195356
Y                                                  51.4561
LONGITUDE                                        -0.195356
LATITUDE                                           51.4561
MESSAGEDATE                            31/12/2014 10:49:25
USERID                                            29823208
USERSCREENNAME                             JeremyGriffiths
MESSAGETEXT           2015 is going to be my year         
LOCATION                                        Wandsworth
HASHTAGS                                               NaN
ISRETWEET                                                0
datetime                               2014-12-31 10:49:25
Cluster                                                  2
parsed_tweets                       is going to be my year
stemmed_tokens               

...

Name: 63542, dtype: object
id                                                   550371807673716736
Name                                                                NaN
X                                                             -0.037168
Y                                                               51.5191
LONGITUDE                                                     -0.037168
LATITUDE                                                        51.5191
MESSAGEDATE                                         31/12/2014 19:23:59
USERID                                                         83952844
USERSCREENNAME                                                BeatWoven
MESSAGETEXT           Thank-u to all that have been part of my 2014!...
LOCATION                                                  Tower Hamlets
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

Name: 73389, dtype: object
id                                                   550355746979061760
Name                                                                NaN
X                                                             -0.317128
Y                                                               51.5786
LONGITUDE                                                     -0.317128
LATITUDE                                                        51.5786
MESSAGEDATE                                         31/12/2014 18:20:09
USERID                                                        188788669
USERSCREENNAME                                             HollieeSarah
MESSAGETEXT           Today is the day millions of people make New Y...
LOCATION                                                          Brent
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

Name: 74332, dtype: object
id                                                   550476352500269056
Name                                                                NaN
X                                                             -0.255857
Y                                                               51.5663
LONGITUDE                                                     -0.255857
LATITUDE                                                        51.5663
MESSAGEDATE                                         01/01/2015 02:19:24
USERID                                                        215363298
USERSCREENNAME                                             weare_br0ken
MESSAGETEXT           @yelyahwilliams @XChadballX I am so so so so s...
LOCATION                                                          Brent
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

Name: 96650, dtype: object
id                                                   550449682678546432
Name                                                                NaN
X                                                              -0.16778
Y                                                               51.4192
LONGITUDE                                                      -0.16778
LATITUDE                                                        51.4192
MESSAGEDATE                                         01/01/2015 00:33:25
USERID                                                        414735661
USERSCREENNAME                                                rebelle82
MESSAGETEXT           Happy New Year!!!!       #drunk #fun #selfie #...
LOCATION                                                         Merton
HASHTAGS                             drunk fun selfie love happynewyear
ISRETWEET                                                             0
datetime                             

Name: 97406, dtype: object
id                                                   550726262122364929
Name                                                                NaN
X                                                             -0.176275
Y                                                                 51.42
LONGITUDE                                                     -0.176275
LATITUDE                                                          51.42
MESSAGEDATE                                         01/01/2015 18:52:27
USERID                                                         40254901
USERSCREENNAME                                              thefashfeed
MESSAGETEXT           A look back over last years popular posts (inc...
LOCATION                                                         Merton
HASHTAGS                                                            NaN
ISRETWEET                                                             0
datetime                             

In [41]:
eastender_tokens = ['eastend','ronni', 'kill','die', 'emma','luci','phil','nick','denis', 'dead']

In [42]:
data["is_eastender_tweet"] = np.nan

In [43]:
data["is_eastender_tweet"] = data.stemmed_tokens.apply(lambda tokens: any(x in tokens for x in eastender_tokens))

In [45]:
eastender_tweets = data[data.is_eastender_tweet == True]

In [46]:
eastender_tweets.to_csv("./data/eastender_tweets.csv")

In [47]:
football_tokens = ['arsen','goal','lampard','wenger','liverpool','team','chelsea','game','kane','spur','harri','tottenham','sunderland','player','leagu','footbal','arsen','mourinho','play','beat','cahil','score']

In [48]:
data["is_football_tweet"] = np.nan

In [49]:
data["is_football_tweet"] = data.stemmed_tokens.apply(lambda tokens: any(x in tokens for x in football_tokens))

In [50]:
football_tweets = data[data.is_football_tweet == True]

In [51]:
football_tweets.to_csv("./data/football_tweets.csv")

In [52]:
football_tweets.head()

id  Name         X          Y  LONGITUDE   LATITUDE  \
0    550226818624942080   NaN -0.262150  51.391407  -0.262150  51.391407   
61   550211786700750849   NaN -0.272859  51.398660  -0.272859  51.398659   
128  550252286908596224   NaN -0.295655  51.384080  -0.295655  51.384079   
147  550245732125777920   NaN -0.257089  51.406690  -0.257089  51.406689   
257  550317344313344000   NaN -0.305016  51.369930  -0.305016  51.369930   

             MESSAGEDATE      USERID USERSCREENNAME  \
0    31/12/2014 09:47:50   113918054   12Elbestreet   
61   31/12/2014 08:48:07  1348662787      Deccers_8   
128  31/12/2014 11:29:03   121374134     aewparsons   
147  31/12/2014 11:03:00     1530791   niallomalley   
257  31/12/2014 15:47:33   335423694  _rachelanstee   

                                           MESSAGETEXT              LOCATION  \
0    @julieo25 Not yet got tics for Liverpool waiti...  Kingston upon Thames   
61   @SkySportsNewsHQ #ssnhqSchurrle The Build Up; ...  Kingston upon Thames   
128  Hope ECB is watching. Only play T20 blast matc...  Kingston upon Thames   
147  @thameswater @Ofwat Hi Tom; any sign of an upd...  Kingston upon Thames   
257  Decided in advance that on valentines day I'm ...  Kingston upon Thames   

           HASHTAGS  ISRETWEET             datetime  Cluster  \
0               NaN          0  2014-12-31 09:47:50        1   
61    ssnhqSchurrle          0  2014-12-31 08:48:07        1   
128  lessonslearned          0  2014-12-31 11:29:03        1   
147             NaN          0  2014-12-31 11:03:00        1   
257             NaN          0  2014-12-31 15:47:33        1   

                                         parsed_tweets  \
0    Not yet got tics for Liverpool waiting till Fr...   
61          The Build Up The Pass The Goal Best For Me   
128  Hope ECB is watching Only play T blast matches...   
147  Hi Tom any sign of an update from the attendin...   
257  Decided in advance that on valentines day I m ...   

                                        stemmed_tokens  is_new_years_tweet  \
0    [not, yet, got, tic, for, liverpool, wait, til...               False   
61   [the, build, Up, the, pass, the, goal, best, f...               False   
128  [hope, ecb, is, watch, onli, play, T, blast, m...               False   
147  [Hi, tom, ani, sign, of, an, updat, from, the,...               False   
257  [decid, in, advanc, that, on, valentin, day, I...               False   

     is_eastender_tweet  is_football_tweet  
0                 False               True  
61                False               True  
128               False               True  
147               False               True  
257               False               True